In [2]:
import pandas  as pd 
from itertools import product
from collections import defaultdict
from itertools import groupby
from copy import deepcopy
import os
import csv
import ast

Estado actual: 
* Pandas es muy lento para lo que quiero hacer
* Trabajo actual: separar los desempates en: Primero wins, despues rounds, despues mapas (probablemente no se implemente)
* Potenciales soluciones: Cambiar la manera de armar la tabla a Numpy (deberia ser lo mas rapido por mucho) Ventajas: velocidad y puedo evaluar por filas los resultados 

-------------------------------------------------------------------------

Arranco casi de 0, problemas con la unicacion de memoria de los objetos y se armo un re quilombo. 
Intento 2 diseño enfocado tabla final que tengo y estructurar desde ese punto hacia atras. 

-------------------------------------------------------------------------

24-1-25
Funcionando en trabajo por lotes. 
Dificultades actuales ordenar los batch para procesarlos. Resto de las funcionalidades parecen ok 


In [3]:
#Esto es raro, siento que estoy dando vueltas en circulo con este diccionario creando los objetos y volviendo a usarlos 
#Lo termino usando con un zip, lo que puede ser peligroso con el orden y las keys
#Agregar h2h ganados aca, voy a tener que modificar como funcionan las fuciones 
teamNameScores = {
                "name": ["Kru","Lev","100T","mibr","NRG","EG","FUR","LOUD", "2G","G2","C9","SEN"],
                "wins": [6,9,5,1,4,4,3,4,7,00,6,6],
                "loss":[4,1,5,9,6,6,7,6,3,00,4,4],
                "matchWins" : [15,19,12,3,10,10,8,11,15,00,13,13],
                "matchLoss" : [10,4,11,18,13,15,15,14,8,00,13,8],
                "roundWin":[287,296,255,168,238,241,195,249,249,00,270,249],
                "roundLoss":[247,204,232,257,237,281,270,275,214,00,276,214],
                'h2h' : [['FUR','mibr','EG','LOUD','C9','SEN'],
                         ['SEN','NRG','G2','100T','EG','LOUD','FUR'],
                         ['EG','G2','NRG'],
                         ['EG'],
                         ['Kru','LOUD','FUR','mibr'],
                         ['SEN','LOUD'],
                         ['100T','mibr'],
                         ['SEN','G2','mibr','100T'],
                         ['FUR','EG','mibr','Kru','NRG','Kru','SEN'],
                         [], 
                         ['Lev','EG','LOUD','FUR','mibr','NRG'],
                         ['100T','mibr','FUR','NRG']
                         ]
                  }

roundMatches = {
                "week11" : [["Kru","Lev"], ["100T","mibr"],["NRG","EG"], ["FUR","LOUD"],["2G","G2"],["C9","SEN"]],
                "week12" : [["Kru","100T"], ["Lev","mibr"],["NRG","FUR"], ["EG","LOUD"],["C9","G2"],["2G","SEN"]]
                }

In [3]:
#Entry vacia para checkear creacion 
teamNameScores = {
    "name": [
        "Kru",
        "Lev",
        "100T",
        "mibr",
        "NRG",
        "EG",
        "FUR",
        "LOUD",
        "2G",
        "GAMERS2",
        "C9",
        "SEN",
    ],
    "wins": [0, 0, 0, 0, 0, 0, 0, 0, 0, 00, 0, 0],
    "loss": [0, 0, 0, 0, 0, 0, 0, 0, 0, 00, 0, 0],
    "matchWins": [0, 0, 0,0, 0, 0,0, 0, 0, 0, 0, 0],
    "matchLoss": [0,0, 0, 0, 0, 0, 0, 0,0, 0, 0, 0],
    "roundWin": [0, 0, 0, 0, 0, 0, 0, 0, 0,0, 0, 0],
    "roundLoss": [0, 0, 0, 0, 0, 0, 0, 0, 0,0, 0, 0],
}

roundMatches = {
    "week11": [
        ["Kru", "Lev"],
        ["100T", "mibr"],
        ["NRG", "EG"],
        ["FUR", "LOUD"],
        ["2G", "GAMERS2"],
        ["C9", "SEN"],
    ],
    "week12": [
        ["Kru", "100T"],
        ["Lev", "mibr"],
        ["NRG", "FUR"],
        ["EG", "LOUD"],
        ["C9", "GAMERS2"],
        ["2G", "SEN"],
    ],
}

In [8]:
def run_round_delta_with_resume(matches, teams, previous_results=None, batch_size=512, output_file="results_part", progress_file="progress.txt"):
    if previous_results is None:
        previous_results = []
        for i, team in enumerate(teams["name"]):
            temp_dict = {
                "UP": 1,
                "Team": team,
                "wins": teams["wins"][i],
                "matchDelta": teams["matchWins"][i] - teams["matchLoss"][i],
                "h2h": teams['h2h'][i]
            }
            previous_results.append(temp_dict)

    match_outcomes = list(product([0, 1, 2, 3], repeat=len(matches)))
    result_mapping = {
        0: (0, 2),
        1: (1, 2),
        2: (2, 1),
        3: (2, 0),
    }

    test_group = defaultdict(list)
    for result in previous_results:
        test_group[result["UP"]].append(result)

    # Leer el progreso guardado
    start_batch = 0
    if os.path.exists(progress_file):
        with open(progress_file, "r") as f:
            start_batch = int(f.read().strip())

    total_batches = len(match_outcomes) // batch_size + 1

    for batch in range(start_batch, total_batches):
        batch_outcomes = match_outcomes[batch * batch_size: (batch + 1) * batch_size]
        new_results = []

        for up, group in test_group.items():
            simul_teams = {
                team_data["Team"]: {
                    "wins": team_data["wins"],
                    "matchDelta": team_data["matchDelta"],
                    'h2h': team_data['h2h']
                }
                for team_data in group
            }

            for combination in batch_outcomes:
                temp_teams = deepcopy(simul_teams)

                for match_index, result in enumerate(combination):
                    team1, team2 = matches[match_index]
                    team1_score, team2_score = result_mapping[result]
                    delta_score = abs(team1_score - team2_score)

                    if result in [2, 3]:
                        temp_teams[team1]["wins"] += 1
                        temp_teams[team1]["matchDelta"] += delta_score
                        temp_teams[team2]["matchDelta"] -= delta_score
                        temp_teams[team1]["h2h"] += [team2]
                    else:
                        temp_teams[team2]["wins"] += 1
                        temp_teams[team2]["matchDelta"] += delta_score
                        temp_teams[team1]["matchDelta"] -= delta_score
                        temp_teams[team2]["h2h"] += [team1]

                new_up = f"{up}-{batch}-{combination}"

                for team, data in temp_teams.items():
                    new_results.append({
                        "UP": new_up,
                        "Team": team,
                        "wins": data["wins"],
                        "matchDelta": data["matchDelta"],
                        'h2h': data['h2h']
                    })

        # Guardado resultados parciales
        output_file_batch = output_file+str(batch)+'.csv'
        df = pd.DataFrame(new_results)
        file_exists = os.path.exists(output_file_batch) and os.path.getsize(output_file_batch) > 0
        df.to_csv(output_file_batch, mode='a', index=False, header=not file_exists)

        # Guardado del progreso
        with open(progress_file, "w") as f:
            f.write(str(batch + 1))

        print(f"Lote {batch + 1}/{total_batches} procesado y guardado.")

    print("Procesamiento completado.")
    os.remove(progress_file) #borrar el progreso si termino de procesar todo 

In [4]:
def groupby_UP(matchresults):
    group_result = defaultdict(list)
    for result in matchresults:
        group_result[result["UP"]].append(result)
    return group_result

def group_table(teamDict) -> list:
    return  [
    list(group) for _, group in groupby(teamDict, key=lambda x: x[1]["wins"])
    ]

def heriarchy_dict_for_sort(groupby_up_dict: dict) -> dict:
    hierarchy_dict_to_return = {}
    for key in groupby_up_dict.keys():
        hierarchy_dict_to_append = {}
        for team in groupby_up_dict[key]:
            hierarchy_dict_to_append[team["Team"]] = {
                "wins": team["wins"],
                "matchDelta": team["matchDelta"],
                'h2h': team['h2h']
            }
        hierarchy_dict_to_return[key] = hierarchy_dict_to_append
    return hierarchy_dict_to_return

def sort_dict_by_wins(single_up_round) -> list:
    count = 1
    sorted_table = sorted(single_up_round.items(), key =lambda x: (x[1]["wins"], x[1]["matchDelta"]), reverse=True)
    
    grouped_table = group_table(sorted_table)
    
    count += 1
    return grouped_table

#Tiebreak Rules

def two_teams_tie(tie_teams: list) -> list: #Esta es rara, falla en tablas incompletas (pueden no haber jugado los dos equipos, pero no deberia falla en la ultima ronda)
    if len(tie_teams) != 2:
        print("not 2 tie teams")
    else:
        team1_h2h_vs_rival = set(tie_teams[0][1]['h2h']) & set([tie_teams[1][0]])

        if len(team1_h2h_vs_rival) == 0:
            tie_teams = tie_teams[1:] + tie_teams[:1]

    return tie_teams

def three_way_tie(tie_teams: list) -> list:
    if len(tie_teams) != 3:
        print('not 3 way tie')
    else:        
        teams = [x[0] for x in tie_teams]
        for index, team  in enumerate(tie_teams): #one team superiority vs the other 2                   
            team_h2h = set(tie_teams[index][1]['h2h']) & set(teams)
    
            if len(team_h2h) == 2:                
                pop_team = tie_teams.pop(index)                                             
                remaining_tie = two_teams_tie(tie_teams)
                tie_teams = [pop_team] + remaining_tie
            
            elif index == 2:
                print('Round diff needed')
        
    return tie_teams

def tiebreaker(tie_teams):
    amount_tie_teams = len(tie_teams)
    if amount_tie_teams >= 4:
        match_tie_set = set()
        for team in tie_teams: #This need to be check
            match_tie_set.add(team[1]["matchDelta"])  
        if amount_tie_teams != match_tie_set:
            pass 
        
    if amount_tie_teams == 3:
        tie_teams = three_way_tie(tie_teams)
        
    if amount_tie_teams == 2:  # Esto se puede cambiar y modificar solo la posición
        
        tie_teams = two_teams_tie(tie_teams)
        
    return tie_teams or []

In [5]:
def untie_round_save(up_dict_sorted,dict_up_position, key):
    positon = 1
    return_dict = []
    for list_team in up_dict_sorted:
        if len(list_team) == 1:                  
            dict_up_position[list_team[0][0]][str(positon)][0] += 1
            dict_up_position[list_team[0][0]][str(positon)][1].add(key)
            positon += 1
            return_dict += [list_team]
        if len(list_team) > 1:           
            sorted_dict_temp = tiebreaker(list_team)
            for team in sorted_dict_temp:
                           
                dict_up_position[team[0]][str(positon)][0] += 1
                dict_up_position[team[0]][str(positon)][1].add(key)
                positon += 1
            return_dict += sorted_dict_temp          
    return return_dict

In [6]:
test_set_dict = {}
for team in teamNameScores["name"]:
    test_set_dict[team] = {
        "1": [0,set()],
        "2": [0,set()],
        "3": [0,set()],
        "4": [0,set()],
        "5": [0,set()],
        "6": [0,set()],
        "7": [0,set()],
        "8": [0,set()],
        "9": [0,set()],
        "10": [0,set()],
        "11": [0,set()],
        "12": [0,set()],

    }

In [7]:
teams = teamNameScores
matches = (("Kru","Lev"), ("100T","mibr"),("NRG","EG"), ("FUR","LOUD"),("2G","G2"),("C9","SEN"))
matches2 = (("Kru","100T"), ("Lev","mibr"),("NRG","FUR"), ("EG","LOUD"),("C9","G2"),("2G","SEN"))

In [10]:
def transform_csv_2_dict(url):
    with open(url, mode='r', encoding='utf-8') as file:
        reader = csv.DictReader(file)
        data = []
        for row in reader:
            data.append({
                "UP": row["UP"], 
                "Team": row["Team"],
                "wins": int(row["wins"]),
                "matchDelta": int(row["matchDelta"]),
                "h2h": ast.literal_eval(row["h2h"])  
            })
    return data

In [11]:
def process_batch(feed_path, result_path, matches, teams, batch_size=512, output_file="result.csv", progress_file="progress.txt"):
    # Listar todos los archivos CSV en el directorio
    files_csv = [archivo for archivo in os.listdir(feed_path) if archivo.endswith(".csv")]

    try:
        os.mkdir(result_path)
        print(f"Directory '{result_path}' created successfully.")
    except FileExistsError:
        print(f"Directory '{result_path}' already exists.")
    except PermissionError:
        print(f"Permission denied: Unable to create '{result_path}'.")
    except Exception as e:
        print(f"An error occurred: {e}")

    for file in files_csv:
        file_path = os.path.join(feed_path, file)  
        print(f"Processing file: {file_path}")
        
        try:
            data = transform_csv_2_dict(file_path)
            file_output = os.path.join(result_path, f"processed_{file}")
            
            run_round_delta_with_resume(
                matches=matches,
                teams=teams,
                previous_results=data,
                batch_size=batch_size,
                output_file=file_output,
                progress_file=progress_file
            )
            
            print(f"File {file} processed and saved to {file_output}.")
        
        except Exception as e:
            print(f"Error processing file {file}: {e}")

In [ ]:
#Process de fecha 1 (se pueden mejorar los paths)
matches = (("Kru", "Lev"), ("100T", "mibr"), ("NRG", "EG"), ("FUR", "LOUD"), ("2G", "G2"), ("C9", "SEN"))
run_round_delta_with_resume(matches, teamNameScores, batch_size=512, output_file=".//results//results_batch_test", progress_file=".//results//progress//progress1.txt")

Lote 1/9 procesado y guardado.
Lote 2/9 procesado y guardado.
Lote 3/9 procesado y guardado.
Lote 4/9 procesado y guardado.
Lote 5/9 procesado y guardado.
Lote 6/9 procesado y guardado.
Lote 7/9 procesado y guardado.
Lote 8/9 procesado y guardado.
Lote 9/9 procesado y guardado.
Procesamiento completado.


In [13]:
#Aca va match2
feed_path = './/results'
path_results = './/results//fecha_2'

process_batch(feed_path,path_results, matches2, teamNameScores, batch_size=512,output_file="result_test.csv",progress_file="progress.txt")

In [ ]:
#procesar lote de resultados: 


In [249]:
path_file = './/results//results_batch_test0.csv' 
data = transform_csv_2_dict(path_file)

In [250]:
groupby_up = groupby_UP(data)

In [251]:
dict_ready_to_sort = heriarchy_dict_for_sort(groupby_up)

In [252]:
dict_ready_to_sort

{'1-0-(0, 0, 0, 0, 0, 0)': {'Kru': {'wins': 6,
   'matchDelta': 3,
   'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']},
  'Lev': {'wins': 10,
   'matchDelta': 17,
   'h2h': ['SEN', 'NRG', 'G2', '100T', 'EG', 'LOUD', 'FUR', 'Kru']},
  '100T': {'wins': 5, 'matchDelta': -1, 'h2h': ['EG', 'G2', 'NRG']},
  'mibr': {'wins': 2, 'matchDelta': -13, 'h2h': ['EG', '100T']},
  'NRG': {'wins': 4, 'matchDelta': -5, 'h2h': ['Kru', 'LOUD', 'FUR', 'mibr']},
  'EG': {'wins': 5, 'matchDelta': -3, 'h2h': ['SEN', 'LOUD', 'NRG']},
  'FUR': {'wins': 3, 'matchDelta': -9, 'h2h': ['100T', 'mibr']},
  'LOUD': {'wins': 5,
   'matchDelta': -1,
   'h2h': ['SEN', 'G2', 'mibr', '100T', 'FUR']},
  '2G': {'wins': 7,
   'matchDelta': 5,
   'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']},
  'G2': {'wins': 1, 'matchDelta': 2, 'h2h': ['2G']},
  'C9': {'wins': 6,
   'matchDelta': -2,
   'h2h': ['Lev', 'EG', 'LOUD', 'FUR', 'mibr', 'NRG']},
  'SEN': {'wins': 7,
   'matchDelta': 7,
   'h2h': ['100T', 'mibr', 'FUR',

In [159]:
def sort_dict_by_wins(single_up_round):
    count = 1
    sorted_table = sorted(single_up_round.items(), key =lambda x: (x[1]["wins"], x[1]["matchDelta"]), reverse=True)
    
    grouped_table = group_table(sorted_table)
    
    count += 1
    return grouped_table
#Aca tengo que agregar el desempate y los resultados y no crear todo la lista larga? 

In [153]:
def two_teams_tie(tie_teams):
    if len(tie_teams) != 2:
        print("not 2 tie teams")
    else:
        team1_h2h_vs_rival = set(tie_teams[0][1]['h2h']) & set([tie_teams[1][0]])

        if len(team1_h2h_vs_rival) == 0:
            tie_teams = tie_teams[1:] + tie_teams[:1]

    return tie_teams

In [154]:
def three_way_tie(tie_teams):
    if len(tie_teams) != 3:
        print('not 3 way tie')
    else:
        
        teams = [x[0] for x in tie_teams]
        for index, team  in enumerate(tie_teams): #one team superiority vs the other 2                   
            team_h2h = set(tie_teams[index][1]['h2h']) & set(teams)
    
            if len(team_h2h) == 2:                
                pop_team = tie_teams.pop(index)                                             
                remaining_tie = two_teams_tie(tie_teams)
                tie_teams = [pop_team] + remaining_tie
            
            elif index == 2:
                print('Round diff needed')

        
    return tie_teams

In [155]:
def tiebreaker(tie_teams):
    amount_tie_teams = len(tie_teams)
    if amount_tie_teams >= 4:
        match_tie_set = set()
        for team in tie_teams: #This need to be check
            match_tie_set.add(team[1]["matchDelta"])  
        if amount_tie_teams != match_tie_set:
            pass 
        
    if amount_tie_teams == 3:
        tie_teams = three_way_tie(tie_teams)
        
    if amount_tie_teams == 2:  # Esto se puede cambiar y modificar solo la posición
        
        tie_teams = two_teams_tie(tie_teams)
        
    return tie_teams or []

In [156]:
def untie(up_dict_sorted,dict_up_position):
    positon = 1
    return_dict = []
    for list_team in up_dict_sorted:
        if len(list_team) == 1:            
            dict_up_position[list_team[0][0]][str(positon)] += 1
            positon += 1
            return_dict += [list_team]
        if len(list_team) > 1:           
            sorted_dict_temp = tiebreaker(list_team)
            for team in sorted_dict_temp:             
                dict_up_position[team[0]][str(positon)] += 1
                positon += 1
            return_dict += sorted_dict_temp          
    return return_dict

In [21]:
dict_up_h2h = {}
for team in teamNameScores["name"]:
    dict_up_h2h[team] = []

In [222]:
dict_up_h2h = {}
for team in teamNameScores["name"]:
    dict_up_h2h[team] = []

dict_up_h2h["Kru"].append("FUR")
dict_up_h2h["Kru"].append("mibr")
dict_up_h2h["Kru"].append("EG")
dict_up_h2h["Kru"].append("LOUD")
dict_up_h2h["Kru"].append("100T")
dict_up_h2h["Kru"].append("C9")
dict_up_h2h["Kru"].append("SEN")

dict_up_h2h["Lev"].append("SEN")
dict_up_h2h["Lev"].append("NRG")
dict_up_h2h["Lev"].append("G2")
dict_up_h2h["Lev"].append("Kru")
dict_up_h2h["Lev"].append("mibr")
dict_up_h2h["Lev"].append("100T")
dict_up_h2h["Lev"].append("EG")
dict_up_h2h["Lev"].append("LOUD")
dict_up_h2h["Lev"].append("FUR")

dict_up_h2h["2G"].append("FUR")
dict_up_h2h["2G"].append("EG")
dict_up_h2h["2G"].append("mibr")
dict_up_h2h["2G"].append("C9")
dict_up_h2h["2G"].append("Kru")
dict_up_h2h["2G"].append("C9")
dict_up_h2h["2G"].append("NRG")
dict_up_h2h["2G"].append("Kru")
dict_up_h2h["2G"].append("SEN")

dict_up_h2h["SEN"].append("100T")
dict_up_h2h["SEN"].append("mibr")
dict_up_h2h["SEN"].append("FUR")
dict_up_h2h["SEN"].append("NRG")
#dict_up_h2h["SEN"].append("Kru")
dict_up_h2h["SEN"].append("C9")

dict_up_h2h["C9"].append("Lev")
dict_up_h2h["C9"].append("EG")
dict_up_h2h["C9"].append("LOUD")
dict_up_h2h["C9"].append("FUR")
dict_up_h2h["C9"].append("mibr")
dict_up_h2h["C9"].append("NRG")

dict_up_h2h["100T"].append("G2")
dict_up_h2h["100T"].append("C9")
dict_up_h2h["100T"].append("NRG")
dict_up_h2h["100T"].append("mibr")
dict_up_h2h["100T"].append("EG")

dict_up_h2h["NRG"].append("LOUD")
dict_up_h2h["NRG"].append("FUR")
dict_up_h2h["NRG"].append("mibr")
dict_up_h2h["NRG"].append("Kru")

dict_up_h2h["LOUD"].append("SEN")
dict_up_h2h["LOUD"].append("G2")
dict_up_h2h["LOUD"].append("mibr")
dict_up_h2h["LOUD"].append("100T")

dict_up_h2h["EG"].append("SEN")
dict_up_h2h["EG"].append("NRG")
dict_up_h2h["EG"].append("LOUD")
dict_up_h2h["EG"].append("FUR")

dict_up_h2h["FUR"].append("100T")
dict_up_h2h["FUR"].append("LOUD")
dict_up_h2h["FUR"].append("mibr")

dict_up_h2h["mibr"].append("EG")



In [254]:
dict_ready_to_sort

{'1-0-(0, 0, 0, 0, 0, 0)': {'Kru': {'wins': 6,
   'matchDelta': 3,
   'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']},
  'Lev': {'wins': 10,
   'matchDelta': 17,
   'h2h': ['SEN', 'NRG', 'G2', '100T', 'EG', 'LOUD', 'FUR', 'Kru']},
  '100T': {'wins': 5, 'matchDelta': -1, 'h2h': ['EG', 'G2', 'NRG']},
  'mibr': {'wins': 2, 'matchDelta': -13, 'h2h': ['EG', '100T']},
  'NRG': {'wins': 4, 'matchDelta': -5, 'h2h': ['Kru', 'LOUD', 'FUR', 'mibr']},
  'EG': {'wins': 5, 'matchDelta': -3, 'h2h': ['SEN', 'LOUD', 'NRG']},
  'FUR': {'wins': 3, 'matchDelta': -9, 'h2h': ['100T', 'mibr']},
  'LOUD': {'wins': 5,
   'matchDelta': -1,
   'h2h': ['SEN', 'G2', 'mibr', '100T', 'FUR']},
  '2G': {'wins': 7,
   'matchDelta': 5,
   'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']},
  'G2': {'wins': 1, 'matchDelta': 2, 'h2h': ['2G']},
  'C9': {'wins': 6,
   'matchDelta': -2,
   'h2h': ['Lev', 'EG', 'LOUD', 'FUR', 'mibr', 'NRG']},
  'SEN': {'wins': 7,
   'matchDelta': 7,
   'h2h': ['100T', 'mibr', 'FUR',

In [255]:
test_sort = sort_dict_by_wins(dict_ready_to_sort["1-0-(0, 0, 0, 0, 0, 0)"])

In [79]:
test_sort

[[('Lev',
   {'wins': 10,
    'matchDelta': 17,
    'h2h': ['SEN', 'NRG', 'G2', '100T', 'EG', 'LOUD', 'FUR', 'Kru']})],
 [('2G',
   {'wins': 7,
    'matchDelta': 5,
    'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']}),
  ('C9',
   {'wins': 7,
    'matchDelta': 1,
    'h2h': ['Lev', 'EG', 'LOUD', 'FUR', 'mibr', 'NRG', 'SEN']})],
 [('SEN', {'wins': 6, 'matchDelta': 4, 'h2h': ['100T', 'mibr', 'FUR', 'NRG']}),
  ('Kru',
   {'wins': 6,
    'matchDelta': 3,
    'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']})],
 [('100T', {'wins': 5, 'matchDelta': -1, 'h2h': ['EG', 'G2', 'NRG']}),
  ('LOUD',
   {'wins': 5, 'matchDelta': -1, 'h2h': ['SEN', 'G2', 'mibr', '100T', 'FUR']}),
  ('EG', {'wins': 5, 'matchDelta': -3, 'h2h': ['SEN', 'LOUD', 'NRG']})],
 [('NRG',
   {'wins': 4, 'matchDelta': -5, 'h2h': ['Kru', 'LOUD', 'FUR', 'mibr']})],
 [('FUR', {'wins': 3, 'matchDelta': -9, 'h2h': ['100T', 'mibr']})],
 [('mibr', {'wins': 2, 'matchDelta': -13, 'h2h': ['EG', '100T']})],
 [('G2', {'wins': 1,

In [85]:
test_sort_2 = untie_round_save(test_sort,test_set_dict,'1-3')

Round diff needed


In [256]:
test_set_dict

{'Kru': {'1': [0, set()],
  '2': [0, set()],
  '3': [0, set()],
  '4': [0, set()],
  '5': [0, set()],
  '6': [0, set()],
  '7': [0, set()],
  '8': [0, set()],
  '9': [0, set()],
  '10': [0, set()],
  '11': [0, set()],
  '12': [0, set()]},
 'Lev': {'1': [0, set()],
  '2': [0, set()],
  '3': [0, set()],
  '4': [0, set()],
  '5': [0, set()],
  '6': [0, set()],
  '7': [0, set()],
  '8': [0, set()],
  '9': [0, set()],
  '10': [0, set()],
  '11': [0, set()],
  '12': [0, set()]},
 '100T': {'1': [0, set()],
  '2': [0, set()],
  '3': [0, set()],
  '4': [0, set()],
  '5': [0, set()],
  '6': [0, set()],
  '7': [0, set()],
  '8': [0, set()],
  '9': [0, set()],
  '10': [0, set()],
  '11': [0, set()],
  '12': [0, set()]},
 'mibr': {'1': [0, set()],
  '2': [0, set()],
  '3': [0, set()],
  '4': [0, set()],
  '5': [0, set()],
  '6': [0, set()],
  '7': [0, set()],
  '8': [0, set()],
  '9': [0, set()],
  '10': [0, set()],
  '11': [0, set()],
  '12': [0, set()]},
 'NRG': {'1': [0, set()],
  '2': [0, set()

In [55]:
match_outcomes = list(product(['0-2', '1-2', '2-1', '2-0'], repeat=6))

In [98]:
dict_ready_to_sort

{'1-1': {'Kru': {'wins': 6,
   'matchDelta': 3,
   'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']},
  'Lev': {'wins': 10,
   'matchDelta': 17,
   'h2h': ['SEN', 'NRG', 'G2', '100T', 'EG', 'LOUD', 'FUR', 'Kru']},
  '100T': {'wins': 5, 'matchDelta': -1, 'h2h': ['EG', 'G2', 'NRG']},
  'mibr': {'wins': 2, 'matchDelta': -13, 'h2h': ['EG', '100T']},
  'NRG': {'wins': 4, 'matchDelta': -5, 'h2h': ['Kru', 'LOUD', 'FUR', 'mibr']},
  'EG': {'wins': 5, 'matchDelta': -3, 'h2h': ['SEN', 'LOUD', 'NRG']},
  'FUR': {'wins': 3, 'matchDelta': -9, 'h2h': ['100T', 'mibr']},
  'LOUD': {'wins': 5,
   'matchDelta': -1,
   'h2h': ['SEN', 'G2', 'mibr', '100T', 'FUR']},
  '2G': {'wins': 7,
   'matchDelta': 5,
   'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']},
  'G2': {'wins': 1, 'matchDelta': 2, 'h2h': ['2G']},
  'C9': {'wins': 6,
   'matchDelta': -2,
   'h2h': ['Lev', 'EG', 'LOUD', 'FUR', 'mibr', 'NRG']},
  'SEN': {'wins': 7,
   'matchDelta': 7,
   'h2h': ['100T', 'mibr', 'FUR', 'NRG', 'C9']}},
 '

In [241]:
dict_ready_to_sort

{'1-0-(0, 0, 0, 0, 0, 0)-0-(0, 0, 0, 0, 0, 0)': {'Kru': {'wins': 6,
   'matchDelta': 1,
   'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']},
  'Lev': {'wins': 11,
   'matchDelta': 19,
   'h2h': ['SEN', 'NRG', 'G2', '100T', 'EG', 'LOUD', 'FUR', 'Kru', 'Kru']},
  '100T': {'wins': 5, 'matchDelta': -3, 'h2h': ['EG', 'G2', 'NRG']},
  'mibr': {'wins': 3, 'matchDelta': -11, 'h2h': ['EG', '100T', '100T']},
  'NRG': {'wins': 4, 'matchDelta': -7, 'h2h': ['Kru', 'LOUD', 'FUR', 'mibr']},
  'EG': {'wins': 6, 'matchDelta': -1, 'h2h': ['SEN', 'LOUD', 'NRG', 'NRG']},
  'FUR': {'wins': 3, 'matchDelta': -11, 'h2h': ['100T', 'mibr']},
  'LOUD': {'wins': 6,
   'matchDelta': 1,
   'h2h': ['SEN', 'G2', 'mibr', '100T', 'FUR', 'FUR']},
  '2G': {'wins': 7,
   'matchDelta': 3,
   'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']},
  'G2': {'wins': 2, 'matchDelta': 4, 'h2h': ['2G', '2G']},
  'C9': {'wins': 6,
   'matchDelta': -4,
   'h2h': ['Lev', 'EG', 'LOUD', 'FUR', 'mibr', 'NRG']},
  'SEN': {'wins': 

In [257]:
for key in dict_ready_to_sort.keys():
    sorted_table = sort_dict_by_wins(dict_ready_to_sort[key])
    untie_round_save(sorted_table,test_set_dict,key)
    print(key)

Round diff needed
1-0-(0, 0, 0, 0, 0, 0)
Round diff needed
1-0-(0, 0, 0, 0, 0, 1)
Round diff needed
1-0-(0, 0, 0, 0, 0, 2)
Round diff needed
1-0-(0, 0, 0, 0, 0, 3)
Round diff needed
1-0-(0, 0, 0, 0, 1, 0)
Round diff needed
1-0-(0, 0, 0, 0, 1, 1)
Round diff needed
1-0-(0, 0, 0, 0, 1, 2)
Round diff needed
1-0-(0, 0, 0, 0, 1, 3)
Round diff needed
1-0-(0, 0, 0, 0, 2, 0)
Round diff needed
1-0-(0, 0, 0, 0, 2, 1)
Round diff needed
1-0-(0, 0, 0, 0, 2, 2)
Round diff needed
1-0-(0, 0, 0, 0, 2, 3)
Round diff needed
1-0-(0, 0, 0, 0, 3, 0)
Round diff needed
1-0-(0, 0, 0, 0, 3, 1)
Round diff needed
1-0-(0, 0, 0, 0, 3, 2)
Round diff needed
1-0-(0, 0, 0, 0, 3, 3)
Round diff needed
1-0-(0, 0, 0, 1, 0, 0)
Round diff needed
1-0-(0, 0, 0, 1, 0, 1)
Round diff needed
1-0-(0, 0, 0, 1, 0, 2)
Round diff needed
1-0-(0, 0, 0, 1, 0, 3)
Round diff needed
1-0-(0, 0, 0, 1, 1, 0)
Round diff needed
1-0-(0, 0, 0, 1, 1, 1)
Round diff needed
1-0-(0, 0, 0, 1, 1, 2)
Round diff needed
1-0-(0, 0, 0, 1, 1, 3)
Round diff neede

In [263]:
#matches
result_mapping = {
        0: '0-2',
        1: '1-2',
        2: '2-1',
        3: '2-0',
    }
result = 0
result_mapping[result]

'0-2'

In [279]:
import re
def extract_parentheses_values(input_string):
    # Valores dentro de parentesis
    pattern = r'\((.*?)\)'
    matches = re.findall(pattern, input_string)
    # Convertir los grupos grupo capturado en una lista de enteros
    results = [list(map(int, match.split(','))) for match in matches]
    return results

In [316]:
for team in test_set_dict:
    for position in test_set_dict[team]:
        print(test_set_dict[team][position])

[0, set()]
[0, set()]
[0, set()]
[512, {'1-0-(0, 1, 0, 3, 2, 2)', '1-0-(0, 0, 3, 0, 3, 0)', '1-0-(0, 0, 1, 3, 0, 2)', '1-0-(0, 1, 3, 1, 3, 0)', '1-0-(0, 1, 3, 3, 3, 0)', '1-0-(0, 1, 3, 0, 1, 2)', '1-0-(0, 1, 0, 0, 2, 0)', '1-0-(0, 0, 2, 2, 1, 2)', '1-0-(0, 1, 3, 1, 2, 3)', '1-0-(0, 1, 3, 3, 0, 1)', '1-0-(0, 0, 1, 3, 1, 1)', '1-0-(0, 1, 2, 2, 1, 0)', '1-0-(0, 0, 3, 3, 1, 2)', '1-0-(0, 0, 1, 2, 3, 0)', '1-0-(0, 0, 2, 3, 3, 3)', '1-0-(0, 1, 1, 2, 2, 2)', '1-0-(0, 0, 2, 3, 1, 3)', '1-0-(0, 0, 3, 0, 2, 0)', '1-0-(0, 0, 2, 3, 0, 3)', '1-0-(0, 1, 2, 2, 0, 0)', '1-0-(0, 0, 3, 2, 0, 2)', '1-0-(0, 0, 0, 0, 2, 2)', '1-0-(0, 0, 2, 1, 0, 3)', '1-0-(0, 0, 2, 0, 3, 2)', '1-0-(0, 1, 0, 1, 1, 3)', '1-0-(0, 1, 0, 0, 3, 1)', '1-0-(0, 0, 2, 1, 3, 2)', '1-0-(0, 1, 3, 2, 2, 2)', '1-0-(0, 0, 3, 1, 1, 0)', '1-0-(0, 1, 0, 3, 2, 3)', '1-0-(0, 0, 1, 0, 0, 0)', '1-0-(0, 0, 0, 0, 1, 2)', '1-0-(0, 0, 3, 2, 3, 1)', '1-0-(0, 1, 2, 1, 3, 3)', '1-0-(0, 0, 0, 1, 3, 3)', '1-0-(0, 0, 2, 3, 0, 1)', '1-0-(0, 1, 3, 0, 1, 3)'

In [323]:
def create_nested_dict(start, end):
    match_results = {}
    for i in range(start, end + 1):
        match_results[str(i)] = {str(j): [] for j in range(6)}
    return match_results

# Crear el diccionario desde 1 hasta 10 como ejemplo
nested_dict = create_nested_dict(1, 4)

print(nested_dict)

{'1': {'0': [], '1': [], '2': [], '3': [], '4': [], '5': []}, '2': {'0': [], '1': [], '2': [], '3': [], '4': [], '5': []}, '3': {'0': [], '1': [], '2': [], '3': [], '4': [], '5': []}, '4': {'0': [], '1': [], '2': [], '3': [], '4': [], '5': []}}


In [ ]:
#Seguir desde aca, armar la estructura para transformar los (0,0,0,0,0,0) en => Team1 X (Resultado) Team y

result_mapping = {
        0: '0-2',
        1: '1-2',
        2: '2-1',
        3: '2-0',
    }

team = 'Kru'

for position in test_set_dict[team]:
    if int(position) < 5:
        nested_dict = create_nested_dict(1, 4)             
        for element in test_set_dict[team][position][1]:
            extracted_element = extract_parentheses_values(element)
            for number, result in enumerate(extracted_element[0]):
                nested_dict[str(position)][str(number)].append((matches[number][0], result_mapping[result], matches[number][1]))


In [340]:
df = pd.DataFrame.from_dict(nested_dict['4'])
df.columns = ['match_1','match_2','match_3','match_4','match_5','match_6']

array([('C9', '2-1', 'SEN'), ('C9', '0-2', 'SEN'), ('C9', '2-0', 'SEN'),
       ('C9', '1-2', 'SEN')], dtype=object)

In [301]:
for i in matches:
    print(i[1])

Lev
mibr
EG
LOUD
G2
SEN


In [100]:
test_set_dict

{'Kru': {'1': [0, set()],
  '2': [512,
   {'1-2051',
    '1-2052',
    '1-2055',
    '1-2056',
    '1-2067',
    '1-2068',
    '1-2071',
    '1-2072',
    '1-2083',
    '1-2084',
    '1-2087',
    '1-2088',
    '1-2099',
    '1-2100',
    '1-2103',
    '1-2104',
    '1-2115',
    '1-2116',
    '1-2119',
    '1-2120',
    '1-2131',
    '1-2132',
    '1-2135',
    '1-2136',
    '1-2147',
    '1-2148',
    '1-2151',
    '1-2152',
    '1-2163',
    '1-2164',
    '1-2167',
    '1-2168',
    '1-2179',
    '1-2180',
    '1-2183',
    '1-2184',
    '1-2195',
    '1-2196',
    '1-2199',
    '1-2200',
    '1-2211',
    '1-2212',
    '1-2215',
    '1-2216',
    '1-2227',
    '1-2228',
    '1-2231',
    '1-2232',
    '1-2243',
    '1-2244',
    '1-2247',
    '1-2248',
    '1-2259',
    '1-2260',
    '1-2263',
    '1-2264',
    '1-2275',
    '1-2276',
    '1-2279',
    '1-2280',
    '1-2291',
    '1-2292',
    '1-2295',
    '1-2296',
    '1-2307',
    '1-2308',
    '1-2311',
    '1-2312',
    '1-23

In [50]:
dict_up_position['Kru']['UP_id']

{'1-547',
 '1-3310',
 '1-1089',
 '1-2441',
 '1-2155',
 '1-3165',
 '1-4095',
 '1-1695',
 '1-2755',
 '1-2869',
 '1-3144',
 '1-691',
 '1-2290',
 '1-1065',
 '1-2823',
 '1-2609',
 '1-3404',
 '1-3188',
 '1-357',
 '1-1697',
 '1-3160',
 '1-475',
 '1-1856',
 '1-3218',
 '1-3244',
 '1-2854',
 '1-1694',
 '1-125',
 '1-2105',
 '1-920',
 '1-2066',
 '1-3007',
 '1-1196',
 '1-1548',
 '1-2631',
 '1-461',
 '1-1445',
 '1-2981',
 '1-2810',
 '1-3194',
 '1-2218',
 '1-3727',
 '1-148',
 '1-2085',
 '1-1494',
 '1-2659',
 '1-1752',
 '1-466',
 '1-41',
 '1-1845',
 '1-2254',
 '1-2776',
 '1-376',
 '1-3372',
 '1-408',
 '1-2991',
 '1-1963',
 '1-1924',
 '1-3274',
 '1-2481',
 '1-2123',
 '1-3497',
 '1-147',
 '1-3676',
 '1-2903',
 '1-3952',
 '1-372',
 '1-776',
 '1-905',
 '1-2204',
 '1-2479',
 '1-2653',
 '1-3189',
 '1-2832',
 '1-1612',
 '1-3082',
 '1-2882',
 '1-1542',
 '1-3554',
 '1-3901',
 '1-3273',
 '1-23',
 '1-1906',
 '1-2622',
 '1-616',
 '1-3019',
 '1-719',
 '1-2686',
 '1-4039',
 '1-3739',
 '1-1708',
 '1-2721',
 '1-3693'

In [140]:
dict_up_position

{'Kru': {'1': 0,
  '2': 512,
  '3': 1536,
  '4': 1920,
  '5': 128,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'Lev': {'1': 4096,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 '100T': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 640,
  '6': 3456,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'mibr': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 4096,
  '12': 0},
 'NRG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 1920,
  '8': 1152,
  '9': 1024,
  '10': 0,
  '11': 0,
  '12': 0},
 'EG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 1536,
  '8': 512,
  '9': 1280,
  '10': 768,
  '11': 0,
  '12': 0},
 'FUR': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 512,
  '9': 1280,
  '10': 2304,
  '11': 0,
  '12': 0},
 'LOUD': {'1': 0,
  '2': 0,
  '3':

In [122]:
untie(test_sort, dict_up_h2h, dict_up_position)

entro
entro
entro en 3


In [124]:
dict_up_position

{'Kru': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 1,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'Lev': {'1': 1,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 '100T': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 1,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'mibr': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 1,
  '12': 0},
 'NRG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 1,
  '10': 0,
  '11': 0,
  '12': 0},
 'EG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 1,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'FUR': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 1,
  '11': 0,
  '12': 0},
 'LOUD': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 1,
  '8

In [120]:
dict_up_position

{'Kru': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 1,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'Lev': {'1': 1,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 '100T': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 1,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'mibr': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 1,
  '12': 0},
 'NRG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 1,
  '10': 0,
  '11': 0,
  '12': 0},
 'EG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 1,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'FUR': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 1,
  '11': 0,
  '12': 0},
 'LOUD': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 1,
  '8

In [124]:
sorted_values = sorted_list_of_up_dict(dict_ready_to_sort)

In [122]:
sorted_result = []

for key in dict_ready_to_sort.keys():
    single_up_sorted = sort_dict_by_wins(dict_ready_to_sort[key])
    sorted_result.append(single_up_sorted)
    

In [121]:
sorted_result

[[[('Lev', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('mibr', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('EG', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('LOUD', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('GAMERS2', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('SEN', {'wins': 1, 'matchWins': 2, 'matchLoss': 0})],
  [('Kru', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('100T', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('NRG', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('FUR', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('2G', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('C9', {'wins': 0, 'matchWins': 0, 'matchLoss': 2})]],
 [[('Lev', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('mibr', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('EG', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('LOUD', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('GAMERS2', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('SEN', {'wins':

In [98]:
round1_df = pd.DataFrame(match1_results)

In [101]:
test_woking = round1_df

In [11]:
match2_results = run_round(matches, teams, match1_results)